In [1]:
# Scraping no Site QuintoAndar
# Camila Junqueira
# Gabriel Nasser
# Rafaela Alexandre
import requests
from bs4 import BeautifulSoup
import json
import re
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from pprint import pprint

In [2]:
def getDadosCEP(cep):
		url = (f'http://www.viacep.com.br/ws/{cep}/json')
		
		req = requests.get(url)
		if req.status_code == 200:
			dados_json = json.loads(req.text)
			return dados_json
		else:
			print('Erro ao buscar CEP')

In [3]:
meu_cep = "04078012"
dados = getDadosCEP(meu_cep)
bairro = dados['bairro']
dados

{'cep': '04078-012',
 'logradouro': 'Avenida Divino Salvador',
 'complemento': 'de 501/502 a 799/800',
 'unidade': '',
 'bairro': 'Planalto Paulista',
 'localidade': 'São Paulo',
 'uf': 'SP',
 'estado': 'São Paulo',
 'regiao': 'Sudeste',
 'ibge': '3550308',
 'gia': '1004',
 'ddd': '11',
 'siafi': '7107'}

In [4]:
bairro = bairro.replace(" ", "-").lower()
bairro

'planalto-paulista'

In [5]:
qa = "https://www.quintoandar.com.br/comprar/imovel/{bairro}-sao-paulo-sp-brasil"

In [6]:
def scraper(bairro):
    driver = webdriver.Chrome()

    driver.get('https://www.quintoandar.com.br/comprar/imovel/'+bairro+'-sao-paulo-sp-brasil')
    time.sleep(5)

    for i in range(9):
        try:
            ver_mais_button = driver.find_element(By.XPATH, "//button[contains(text(), 'Ver mais')]")
            ver_mais_button.click()  # Clica no botão
            time.sleep(3)  # Aguarde o conteúdo carregar após o clique
        except:
            pass

    html_content = driver.page_source
    soup = BeautifulSoup(html_content, 'html.parser')
    soup = soup.find('html')
    soup = soup.prettify()
    return soup

In [7]:
moema = scraper(bairro)
pprint(moema)

('<html lang="pt-BR">\n'
 ' <head>\n'
 '  <style>\n'
 '   '
 '.LGLeeN-keyboard-shortcuts-view{display:-webkit-box;display:-webkit-flex;display:-moz-box;display:-ms-flexbox;display:flex}.LGLeeN-keyboard-shortcuts-view '
 'table,.LGLeeN-keyboard-shortcuts-view tbody,.LGLeeN-keyboard-shortcuts-view '
 'td,.LGLeeN-keyboard-shortcuts-view '
 'tr{background:inherit;border:none;margin:0;padding:0}.LGLeeN-keyboard-shortcuts-view '
 'table{display:table}.LGLeeN-keyboard-shortcuts-view '
 'tr{display:table-row}.LGLeeN-keyboard-shortcuts-view '
 'td{-moz-box-sizing:border-box;box-sizing:border-box;display:table-cell;color:#000;padding:6px;vertical-align:middle;white-space:nowrap}.LGLeeN-keyboard-shortcuts-view '
 'td:first-child{text-align:end}.LGLeeN-keyboard-shortcuts-view td '
 'kbd{background-color:#e8eaed;border-radius:2px;border:none;-moz-box-sizing:border-box;box-sizing:border-box;color:inherit;display:inline-block;font-family:Google '
 'Sans Text,Roboto,Arial,sans-serif;line-height:16px;m

In [8]:
soup = BeautifulSoup(moema, 'html.parser')
casas = soup.find_all(attrs={"data-testid": "house-card-container"})
casas[0]

<div data-testid="house-card-container">
<a class="StyledLink_styledLink__P_6FN" href="/imovel/893507503/comprar/apartamento-2-quartos-planalto-paulista-sao-paulo?from_route=%22search_results%22&amp;house_tags=buyRented&amp;house_tags=newAd&amp;search_id=%22d8b459ff-77f2-467d-bf1e-59dc0bd95bad%22&amp;search_rank=%7B%22sortMode%22%3A%22relevance%22%2C%22searchMode%22%3A%22list%22%2C%22resultsOrigin%22%3A%22search%22%2C%22rank%22%3A0%2C%22personalization%22%3Atrue%7D" target="_blank" title="Apartamento à venda com 2 quartos, 65m² em Planalto Paulista, São Paulo">
<div aria-label="Apartamento . Compre já alugado, Anúncio novo. Planalto Paulista, São Paulo, Avenida Ireré. 65 metros quadrados, 2 quartos, 1 vaga de garagem.  R$ 768 Condo. + IPTU, R$ 450.000 ." class="Cozy__FindHouseCard-Container qHIgfb CsxKHh" role="group" tabindex="0">
<div aria-live="polite" class="Cozy__CardBlock-Container _2pfuCF znH6Fs">
<div class="Cozy__CardRow-Container oVdjIf" role="complementary" style="--card-row

In [9]:
rua = casas[0].find("div", class_="Cozy__FindHouseCard-Container").text
rua = rua.split("São Paulo")[0].split('\n\n')[-1].lstrip()
rua = rua.split(",")[0]
rua

'Avenida Ireré'

In [10]:
def find_rua_imovel(imovel):
    rua = imovel.find("div", class_="Cozy__FindHouseCard-Container").text
    rua = rua.split("São Paulo")[0].split('\n\n')[-1].lstrip()
    rua = rua.split(",")[0]
    return rua

In [11]:
valor = casas[0].find("div", class_="Cozy__FindHouseCard-Container").text
valor = valor.split("R$")[1]
valor = re.sub(r'\D', '', valor)
valor

'450000'

In [12]:
img_tag = casas[0].find('img', class_='ProgressiveImage_image__1QoR0')
alt_text = img_tag['alt']
alt_text = alt_text.split("m²")[0].split(" ")
alt_text[-1]


'65'

In [13]:
def find_preco_imovel(imovel):
    valor = imovel.find("div", class_="Cozy__FindHouseCard-Container").text
    valor = valor.split("R$")[1]
    return re.sub(r'\D', '', valor)

In [14]:
find_preco_imovel(casas[0])

'450000'

In [15]:
def find_m2_imovel(imovel):
    img_tag = imovel.find('img', class_='ProgressiveImage_image__1QoR0')
    alt_text = img_tag['alt']
    alt_text = alt_text.split("m²")[0].split(" ")
    return alt_text[-1]
    

In [16]:
find_m2_imovel(casas[0])

'65'

In [17]:
for i in range(0, 30):
    print("Preco: " + find_preco_imovel(casas[i]))
    print("m2: " + find_m2_imovel(casas[i]))
    print("-"*10)

Preco: 450000
m2: 65
----------
Preco: 387000
m2: 50
----------
Preco: 593000
m2: 80
----------
Preco: 1490000
m2: 210
----------
Preco: 400000
m2: 70
----------
Preco: 675000
m2: 144
----------
Preco: 799000
m2: 120
----------
Preco: 765000
m2: 140
----------
Preco: 610000
m2: 95
----------
Preco: 455000
m2: 75
----------
Preco: 460000
m2: 96
----------
Preco: 445000
m2: 69
----------
Preco: 599000
m2: 128
----------
Preco: 1400000
m2: 220
----------
Preco: 800000
m2: 150
----------
Preco: 1427000
m2: 205
----------
Preco: 200000
m2: 18
----------
Preco: 800000
m2: 150
----------
Preco: 1900000
m2: 320
----------
Preco: 438000
m2: 60
----------
Preco: 320000
m2: 27
----------
Preco: 1100000
m2: 230
----------
Preco: 1425000
m2: 250
----------
Preco: 426000
m2: 58
----------
Preco: 2975000
m2: 457
----------
Preco: 1240000
m2: 130
----------
Preco: 1060000
m2: 300
----------
Preco: 355000
m2: 32
----------
Preco: 535000
m2: 120
----------
Preco: 430000
m2: 57
----------


In [18]:
import sqlite3

In [19]:
conn = sqlite3.connect('data.db')
cursor = conn.cursor()

In [20]:
cursor.execute('''
CREATE TABLE IF NOT EXISTS data (
    id INTEGER PRIMARY KEY AUTOINCREMENT,
    cep TEXT NOT NULL,
    rua TEXT NOT NULL,
    bairro TEXT NOT NULL,
    cidade TEXT NOT NULL,
    estado TEXT NOT NULL,
    regiao TEXT NOT NULL,
    preco FLOAT NOT NULL,
    m2 FLOAT NOT NULL,
    preco_m2 FLOAT NOT NULL
)
''')

In [21]:
def add_data(cep, rua, bairro, cidade, estado, regiao, preco, m2, preco_m2):
    cursor.execute('''
    INSERT INTO data (cep, rua, bairro, cidade, estado, regiao, preco, m2, preco_m2) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?)
    ''', (cep, rua, bairro, cidade, estado, regiao, preco, m2, preco_m2))
    conn.commit()

In [22]:
def remove_data(id):
    cursor.execute('''
    DELETE FROM data WHERE id = ?
    ''', (id,))
    conn.commit()

In [23]:
def get_id(cep):
    cursor.execute('''
    SELECT id FROM data WHERE cep = ?
    ''', (cep,))
    data = cursor.fetchall()
    return data

In [24]:
def extract_data(cep):
    dados = getDadosCEP(cep)
    bairro = dados['bairro']
    cidade = dados['localidade']
    estado = dados['uf']
    regiao = dados['regiao']
    bairro = bairro.replace(" ", "-").lower()
    soup = scraper(bairro)
    soup = BeautifulSoup(soup, 'html.parser')
    casas = soup.find_all(attrs={"data-testid": "house-card-container"})
    for casa in casas:
        preco = find_preco_imovel(casa)
        m2 = find_m2_imovel(casa)
        rua = find_rua_imovel(casa)
        preco_m2 = float(preco) / float(m2)
        
        # Check if the data already exists
        cursor.execute('''
        SELECT id FROM data 
        WHERE cep = ? AND bairro = ? AND preco = ? AND m2 = ?
        ''', (cep, bairro, preco, m2))
        
        if cursor.fetchone() is None:
            # Data doesn't exist, so insert it
            add_data(cep, rua, bairro, cidade, estado, regiao, preco, m2, preco_m2)

In [25]:
extract_data("04078012")

In [26]:
def delete_all():
    cursor.execute('''
    DELETE FROM data
    ''')
    conn.commit()

In [27]:
# delete_all()
# Limpar banco de dados para teste 

In [28]:
def precos_medios():
    cursor.execute('''
    SELECT bairro, AVG(preco_m2) AS preco_medio_m2
    FROM data
    GROUP BY bairro
    ''')
    return cursor.fetchall()

In [29]:
extract_data("04119010")

In [30]:
precos_medios()

[('moema', 15195.022755120612),
 ('planalto-paulista', 7944.554860997816),
 ('vila-dom-pedro-i', 10813.997178278072),
 ('vila-mariana', 1731168.6372411228)]

In [31]:
for bairro, preco_medio_m2 in precos_medios():
    print(f"Bairro: {bairro} - Preço médio por m²: R${preco_medio_m2:.2f}")

Bairro: moema - Preço médio por m²: R$15195.02
Bairro: planalto-paulista - Preço médio por m²: R$7944.55
Bairro: vila-dom-pedro-i - Preço médio por m²: R$10814.00
Bairro: vila-mariana - Preço médio por m²: R$1731168.64
